In [1]:
from read_lastfm import read_lastfm
from datetime import datetime
import requests
import json
import urllib.parse
import pandas as pd
import threading

API_KEY1 = '471bf4b3afffd1b470553bbc6b26bef8'
API_KEY2 = '8d24d2f39a2225b2c41c96ed642a0043'

In [2]:
if False:
    songs['song_id'] = songs.track_name.cat.codes + songs.artist_name.cat.codes * 2e6
    top_songs = songs.groupby("song_id").count()
    top_songs = top_songs[['user_id']].reset_index().rename(columns={"user_id":"count"})
    ordered_discography = songs[['track_name', 'artist_name', 'song_id']].drop_duplicates()\
                    .merge(top_songs, how='left').sort_values("count", ascending=False)
#     ordered_discography.to_csv("ordered_discography.csv", index=False)
else:
    ordered_discography = pd.read_csv("ordered_discography.csv")
    split = len(ordered_discography) // 2
    df1 = ordered_discography.iloc[:split]
    df2 = ordered_discography.iloc[split:]

In [3]:
# songs, users = read_lastfm()

In [4]:
# songs.head()

In [5]:
def getTrackTags(artist=None, track=None, track_id=None, threshold=10, key=1):
    artist = urllib.parse.quote(artist)
    track = urllib.parse.quote(track)
    api_key = API_KEY1 if key == 1 else API_KEY2
    url = f"http://ws.audioscrobbler.com/2.0/?method=track.gettoptags&artist={artist}&track={track}&api_key={api_key}&format=json&autocorrect=1"
    response = requests.get(url).json()
    if 'error' not in response:
        return response['toptags']['tag']
    else:
        return response

In [6]:
def extract_track_tag(df, threadID=0, key=1):
    data = []
    exception = "None"
    for i, row in df.iterrows():
        artist = row['artist_name']
        track = row['track_name']
        try:
            res = getTrackTags(artist, track, key)
            if 'error' in res:
                print(f'Exception at index {i}, for {artist} - {track}: {res["message"]}')
                if "Rate Limit Exceeded" in res['message']:
                    exception = "Rate Limit Exceeded"
                    break
                data.append([artist, track, []])
            else:
                data.append([artist, track, res])
        except Exception as e:
            exception = e
            print(f'Exception at index {i}, for {artist} - {track}')
            continue
    tags = pd.DataFrame(data=data, columns=['artist_name', 'track_name', 'tags'])
    tags.to_csv(f"data/song_tags_{threadID}.csv", index=False)
    return exception

In [7]:
class myThread (threading.Thread):
    def __init__(self, threadID, df, key):
        threading.Thread.__init__(self)
        self.threadID = threadID
        self.df = df
        self.key = key
        
    def run(self):
        print (f"Starting {self.threadID} at time {datetime.now().strftime('%H:%M:%S')}")
        exception = extract_track_tag(self.df, self.threadID, key=self.key)
        print (f"Exiting {self.threadID} at time {datetime.now().strftime('%H:%M:%S')} with exception {exception}")

def start_multithreading(df, nb_thread = 2, key=1):
    indices = range(len(df))
    slices = [indices[i::nb_thread] for i in range(nb_thread)]
    for i in range(nb_thread):
        thread = myThread(f"{key}.{i}", df.iloc[slices[i]], key)
        thread.start()

In [14]:
len(df2)*2

1498718

In [13]:
start_multithreading(df2, 2, key=2)

Starting 2.0 at time 16:21:36
Starting 2.1 at time 16:21:37
Exception at index 749376, for Yeah Yeah Yeahs - De Ja Vu [Uk Bonus Track]: Track not found
Exception at index 749384, for Legion Of The Damned - System: Track not found
Exception at index 749456, for Moss - Gate Iii: Devils From The Outer Dark [I) Walpurgis, Ii) The Coming Of 13, Iii)…: Track not found
Exception at index 749489, for V/A: Chrome Children - Med - All I Know: Track not found
Exception at index 749505, for V/A: Weasel Walter Hott Mix Club #7 - No Wave Rarities 1977-1982 - Teenage Jesus - Title Unknown [Live 1977]: Track not found
Exception at index 749602, for Владимир Давидович Ашкенази - Waltz In C Sharp Minor, Op. 64 No.2: Track not found
Exception at index 749621, for V/A: Weasel Walter Hott Mix Club #6 - Ladies Choice - Gilbert Amy - Diaphonies [Edit]: Track not found
Exception at index 749689, for V/A: Planet V - Ed Rush & Optical - Funktion [Remix]: Track not found
Exception at index 749699, for Wolfgang A

Exception at index 751974, for V/A: Fenriz Presents... The Best Of Old-School Black Metal - Venom - Warhead: Track not found
Exception at index 751984, for Tony Franklin - Thirty Days: Track not found
Exception at index 751992, for V/A: We Reach - Mare - Nightgoat: Track not found
Exception at index 752030, for Dr. Krapula - 11 La Fuerza Del Amor 1: Track not found
Exception at index 752130, for V/A: Fenriz Presents... The Best Of Old-School Black Metal - Celtic Frost - Dawn Of Megiddo: Track not found
Exception at index 752146, for Sleeper 1 - Booklung: Track not found
Exception at index 752158, for V/A: Demo-Lition Metal, Vol. 1: American Hell - Hallows Eve - Metal Merchants [From 1984 Demo]: Track not found
Exception at index 752085, for V/A: Zen Rmx - Fog - Pneumonia [Coldcut Mix]: Track not found
Exception at index 752115, for Legion Of The Damned - Dead Cell: Track not found
Exception at index 752171, for Pavle Aksentijevic & Grupa Zapis - Rasla Mi, Rasla, Titra I Nerandža: Track

Exception at index 754530, for Moneyshot - Dj_Moneyshot_Wax_Crackle_And_Pop_Show: Track not found
Exception at index 754463, for V/A: Rise Above - No Value - Hank Iii: Track not found
Exception at index 754489, for V/A: Weasel Walter Hott Mix Club #2 - Metal Hell - Immortal - Battles In The North: Track not found
Exception at index 754549, for Rick Henrickson - Heartbeats: Track not found
Exception at index 754619, for V/A: Pharmacopeia - Rawradarwar - Police Bastard: Track not found
Exception at index 754657, for V/A: Demo-Lition Metal, Vol. 1: American Hell - Rotting Corpse - Rotting Corpse [From 1986 Demo]: Track not found
Exception at index 754675, for Soundtrack - Main Title (Love Theme From 'Lolita') (Film Version From 'Lolita', 1962): Track not found
Exception at index 754754, for Theatre Of Voices - Kill Your Girlfriend (Dead): Track not found
Exception at index 754786, for The Spectre - The Messiah Unknown: Track not found
Exception at index 754719, for [Musical] - Hakuna Mata

Exception at index 756758, for Mambo All-Stars - Godfather (Six Step Mix): Track not found
Exception at index 756667, for Mambo All-Stars - You Dead Wrong: Track not found
Exception at index 756790, for Ron Levy - From Morning Service: Track not found
Exception at index 756695, for 王威登 - Teatro: Track not found
Exception at index 756729, for 王威登 - Eu Não Matei Um Kennedy: Track not found
Exception at index 756751, for Mambo All-Stars - Fonky President: Track not found
Exception at index 756880, for 王威登 - A Crise: Track not found
Exception at index 756789, for V/A: Demo-Lition Metal, Vol. 1: American Hell - Anialator - Nuclear Destruction [From 1988 Demo]: Track not found
Exception at index 756809, for Various Artists - Cinderela - A Sereia De Biquini (1961): Track not found
Exception at index 756883, for 王威登 - Divã De Sangue: Track not found
Exception at index 757004, for V/A: Soundbombing Ii - Dilated Peoples & Tash - Soundbombing: Track not found
Exception at index 756909, for 王威登 - 

Exception at index 758651, for Fools Face - They'Ll Never Know: Track not found
Exception at index 758896, for V/A: Fenriz Presents... The Best Of Old-School Black Metal - Mercyful Fate - Evil: Track not found
Exception at index 758902, for V/A: Fenriz Presents... The Best Of Old-School Black Metal - Nattefrost - Sluts Of Hell: Track not found
Exception at index 758823, for David Cross - Although Indigent Rural Families Have Little To Say In The Matter Third Rate Public…: Track not found
Exception at index 758837, for V/A: The Unsung Heroes [Mixed By Dj Clever] - Electrosoul System - Absolute Zero: Track not found
Exception at index 758861, for Rejoice Singers And Orchestra - There'S A Hole In My Christmas Stocking: Track not found
Exception at index 758978, for Various Artists - Fania All Stars - Bamboleo: Track not found
Exception at index 759002, for Matthew Ward - Sweet Memory / Mystery Of Life: Track not found
Exception at index 759058, for Andrea Bocelli - Andrea Bocelli - Tu Ca 

...

Exception at index 1491141, for Dave Brubeck - Thatoldblackmagic(Johnnymercer,Haroldarlen;Ca1950-1,Thedavebrubecktrio,Sanfrancisco,…: Track not found
Exception at index 1491242, for Miami Lover'S - That Love (Paul Sander Extended Mix): Track not found
Exception at index 1491209, for Dave Wesley - I Can'T Wait (Original Club Radio Edit): Track not found
Exception at index 1491213, for Lavinia Jones - This Aint A Love Song (Live): Track not found
Exception at index 1491298, for Soulseekerz Feat Kate Smith - Party For The Weekend (Stonebridge Radio Edit): Track not found
Exception at index 1491300, for Kidro Feat Double Exposure - Talk Of The Love (Radio Edit): Track not found
Exception at index 1491227, for Kristine W - Walk Away (Tony Moran Club Mix): Track not found
Exception at index 1491241, for Star Tatooed & Ava - Make Me High (Original Radio Edit): Track not found
Exception at index 1491318, for Jose Amnesia (Feat. Jennifer Rene) - Louder (Blake Jarrell'S 190Db Radio Mix): Track n

Exception at index 1492546, for Kyiv Chamber Choir - Chesnokov: To The Holy Virgin We Pray: Track not found
Exception at index 1492562, for Владимир Давидович Ашкенази - 08-Mussorgsky__Bilder_Einer_Ausstellung_Orchesterfassung_2_Promenade_Das_Alte_Schloss: Track not found
Exception at index 1492564, for Владимир Давидович Ашкенази - 10-Mussorgsky__Bilder_Einer_Ausstellung_Orchesterfassung_4_Promenade_Ballet_Der_Kchl…: Track not found
Exception at index 1492493, for Locker Rocket - Rock Rocket_Roqueiros Tambem Amam: Track not found
Exception at index 1492578, for Gleusteen And Ordronneau - Edvard Grieg, Violin Sonata No. 3 In C Minor, Op 45, Allegretto Espressivo Alla…: Track not found
Exception at index 1492505, for 關正傑 - Illusion: Track not found
Exception at index 1492588, for In Camera - Carolan'S Farewell To Music (Carolan, Five Tunes By The Irish Harper): Track not found
Exception at index 1492511, for Locker Rocket - Loucademais_Mixbombada: Track not found
Exception at index 1492

Exception at index 1493213, for In Camera - Carolan'S Draught (Carolan, Five Tunes By The Irish Harper): Track not found
Exception at index 1493289, for Sacred Sin - Sequasutra: Track not found
Exception at index 1493291, for Sacred Sin - Psarchosys: Track not found
Exception at index 1493293, for Sabretooth - Fakeit: Track not found
Exception at index 1493315, for Claire Austin - Sector Xi - As Free As A Bird ~ A Sector Of Mountains: Track not found
Exception at index 1493450, for Death Valley Surfers - Black Pearl: Track not found
Exception at index 1493475, for Fifth Element - Filament: Track not found
Exception at index 1493536, for Fifth Element - Toubkal: Track not found
Exception at index 1493626, for Alaska! - Nunca Se Sabe: Track not found
Exception at index 1493571, for Unreal Project - Changes: Track not found
Exception at index 1493690, for 夢劇院 - Infinite: Track not found
Exception at index 1493700, for Alaska! - Mujeres Rusas: Track not found
Exception at index 1493645, fo

Exception at index 1496079, for The Bug - Let'S Go: Track not found
Exception at index 1496091, for The Bug - Stupid, Stupid: Track not found
Exception at index 1496231, for The Bug - Ai No Uta: Track not found
Exception at index 1496233, for 七三式 - Sakura -New Version-: Track not found
Exception at index 1496247, for The Bug - Bijuu -Beautyful Beast-: Track not found
Exception at index 1496283, for Katharia - Archives Of Doubt I) There Is A Piece Of Gold In All Of My Scars Ii) Borderline…: Track not found
Exception at index 1496338, for The Bug - 1/2: Track not found
Exception at index 1496367, for 聖飢魔Ⅱ - Talk-3 Kayo Mandan: Track not found
Exception at index 1496387, for The Bug - So Crazy: Track not found
Exception at index 1496446, for メリー - Slow-Dive: Track not found
Exception at index 1496460, for The Bug - (You Are) My Pleasure: Track not found
Exception at index 1496455, for The Bug - Jellyfish: Track not found
Exception at index 1496512, for The Bug - Heartache: Track not found

Exception at index 1497593, for Владимир Давидович Ашкенази - Prelude In D Flat Major, Op. 32 No. 13: Track not found
Exception at index 1497595, for Владимир Давидович Ашкенази - Prelude In G Minor, Op. 23 No. 5: Track not found
Exception at index 1497597, for Владимир Давидович Ашкенази - Piano Concerto No. 2 In C Minor, Op. 18 (Allegro Scherzando): Track not found
Exception at index 1497657, for 山本淳一 - Am: Track not found
Exception at index 1497718, for Пётр Ильич Чайковский - Nutcracker Suite - Dance Of The Sugar-Plum Fairy: Track not found
Exception at index 1497683, for Fort Knox Five - Brazilian Hipster (Dr Rubberfunk Mix): Track not found
Exception at index 1497788, for Carlos De Seixas - 06 " " ": Track not found
Exception at index 1497800, for Carlos De Seixas - Keyboard Sonatas: No1 In C: Track not found
Exception at index 1497862, for [Television Theme Songs] - Austin Powers - Theme: Track not found
Exception at index 1497815, for Gottfried Heinrich Stölzel - Ré Maior 1: Tr

In [60]:
# start_multithreading(df2.iloc[:2000], 2, key=2)

Starting 2.0 at time 20:48:53
Starting 2.1 at time 20:48:53
Exception at index 749376, for Yeah Yeah Yeahs - De Ja Vu [Uk Bonus Track]: Track not found
Exception at index 749384, for Legion Of The Damned - System: Track not found
Exception at index 749456, for Moss - Gate Iii: Devils From The Outer Dark [I) Walpurgis, Ii) The Coming Of 13, Iii)…: Track not found
Exception at index 749489, for V/A: Chrome Children - Med - All I Know: Track not found
Exception at index 749505, for V/A: Weasel Walter Hott Mix Club #7 - No Wave Rarities 1977-1982 - Teenage Jesus - Title Unknown [Live 1977]: Track not found
Exception at index 749602, for Владимир Давидович Ашкенази - Waltz In C Sharp Minor, Op. 64 No.2: Track not found
Exception at index 749621, for V/A: Weasel Walter Hott Mix Club #6 - Ladies Choice - Gilbert Amy - Diaphonies [Edit]: Track not found
Exception at index 749689, for V/A: Planet V - Ed Rush & Optical - Funktion [Remix]: Track not found
Exception at index 749699, for Wolfgang A